# Explorando tendencias de mercado de Airbnb

La ciudad de Nueva York tiene una variedad de anuncios de Airbnb para satisfacer la alta demanda de alojamiento temporal para viajeros, con diferentes niveles de precios, tipos de habitaciones y ubicaciones.

La ciudad de Nueva York, es una de las ciudades más visitadas del mundo. Hay muchos anuncios de Airbnb en la ciudad de Nueva York para satisfacer la alta demanda de alojamiento temporal para viajeros, que puede durar desde unas pocas noches hasta muchos meses. En este proyecto, analizaremos más de cerca el mercado de Airbnb de Nueva York combinando datos de varios tipos de archivos como .csv, .tsv y .xlsx.

Recuerde que los archivos CSV, TSV y Excel son tres formatos comunes para almacenar datos. Tiene a su disposición [tres archivos](https://tajamar365.sharepoint.com/:f:/s/3405-MasterIA2024-2025/EoXMgjAJLLNJqWDyKDig8kABSUkpWj_HGQjl267qNnHS9g?e=foxjFc) que contienen datos sobre los anuncios de Airbnb de 2019:  

- `airbnb_price.csv `: Este es un archivo CSV que contiene datos sobre precios y ubicaciones de anuncios de Airbnb.  
  1. `listing_id`: identificador único del anuncio  
  2. `price`: precio del anuncio por noche en USD  
  3. `nbhood_full`: nombre del distrito y del barrio donde se encuentra el anuncio  
    

- `airbnb_room_type.xlsx`: Este es un archivo Excel que contiene datos sobre las descripciones de los anuncios de Airbnb y los tipos de habitaciones.  
  1. `listing_id`: identificador único del anuncio  
  2. `description`: descripción del anuncio     
  3. `room_type`: Airbnb tiene tres tipos de habitaciones: habitaciones compartidas, habitaciones privadas y casas o apartamentos completos 


- `airbnb_last_review.tsv`: Este es un archivo TSV que contiene datos sobre los nombres de los anfitriones de Airbnb y las fechas de revisión.  
  1. `listing_id`: identificador único del anuncio  
  2. `host_name`:  nombre del anfitrión del anuncio  
  3. `last_review`: echa en la que se revisó el anuncio por última vez   

Como consultor que trabaja para una empresa inmobiliaria emergente, ha recopilado datos de anuncios de Airbnb de varias fuentes para investigar el mercado de alquileres a corto plazo en Nueva York. Analizará estos datos para brindar información sobre habitaciones privadas a la empresa inmobiliaria.

- ¿Cuáles son las fechas de las primeras y las últimas reseñas? Almacene estos valores como dos variables independientes con los nombres que prefiera.
- ¿Cuántos de los anuncios son habitaciones privadas? Guárdelo en cualquier variable.
- ¿Cuál es el precio promedio de los anuncios? Redondee a los dos decimales más cercanos y guárdelo en una variable.
- Combine las nuevas variables en un DataFrame llamado review_dates con cuatro columnas en el siguiente orden: first_reviewed, last_reviewed, nb_private_rooms y avg_price. El DataFrame solo debe contener una fila de valores.

In [0]:
dbfs:/FileStore/airbnb_last_review.tsv
dbfs:/FileStore/airbnb_price.csv
dbfs:/FileStore/Caso_3.ipynb
dbfs:/FileStore/airbnb_room_type.xlsx

In [0]:
!pip install openpyxl
!pip install --upgrade pip


[notice] A new release of pip available: 22.2.2 -> 24.3.1
[notice] To update, run: pip install --upgrade pip
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 11.2 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 22.2.2
    Uninstalling pip-22.2.2:
      Successfully uninstalled pip-22.2.2


In [0]:
# Leer los DataFrames
df = spark.read.option("header", "true").option("inferSchema", "true").csv('dbfs:/FileStore/airbnb_price.csv')
# Leer el DataFrame df2 desde un archivo TSV
df2 = spark.read.option("header", "true").option("inferSchema", "true").option("delimiter", "\t").csv('dbfs:/FileStore/airbnb_last_review.tsv')
# Leer el excel
df_xlsx = spark.read.format("com.crealytics.spark.excel").option("dataAddress", "Sheet1").option("header", "true").option("inferSchema", "true").load("dbfs:/FileStore/airbnb_room_type.xlsx")

df.printSchema()
df2.printSchema()
df_xlsx.printSchema()


# Unir df y df2 por listing_id
combined_df = df.join(df2, on="listing_id", how="inner")  # Cambia "inner" a "left", "right" o "outer" según necesites

# Unir el resultado con df3
combined_df = combined_df.join(df3, on="listing_id", how="inner")  # Cambia el tipo de unión si es necesario

# Mostrar el DataFrame combinado
combined_df.display()





root
 |-- listing_id: integer (nullable = true)
 |-- price: string (nullable = true)
 |-- nbhood_full: string (nullable = true)

root
 |-- listing_id: integer (nullable = true)
 |-- host_name: string (nullable = true)
 |-- last_review: string (nullable = true)

root
 |-- listing_id: double (nullable = true)
 |-- description: string (nullable = true)
 |-- room_type: string (nullable = true)



listing_id price nbhood_full host_name last_review description room_type 2595 225 dollars Manhattan, Midtown Jennifer May 21 2019 Skylit Midtown Castle Entire home/apt 3831 89 dollars Brooklyn, Clinton Hill LisaRoxanne July 05 2019 Cozy Entire Floor of Brownstone Entire home/apt 5099 200 dollars Manhattan, Murray Hill Chris June 22 2019 Large Cozy 1 BR Apartment In Midtown East Entire home/apt 5178 79 dollars Manhattan, Hell's Kitchen Shunichi June 24 2019 Large Furnished Room Near B'way private room 5238 150 dollars Manhattan, Chinatown Ben June 09 2019 Cute & Cozy Lower East Side 1 bdrm Entire home/apt 5295 135 dollars Manhattan, Upper West Side Lena June 22 2019 Beautiful 1br on Upper West Side Entire home/apt 5441 85 dollars Manhattan, Hell's Kitchen Kate June 23 2019 Central Manhattan/near Broadway Private room 5803 89 dollars Brooklyn, South Slope Laurie June 24 2019 Lovely Room 1, Garden, Best Area, Legal rental Private room 6021 85 dollars Manhattan, Upper West Side Claudio July 05 2019 Wonderful Guest Bedroom in Manhattan for SINGLES Private room 6848 140 dollars Brooklyn, Williamsburg Allen & Irina June 29 2019 Only 2 stops to Manhattan studio entire home/apt 7097 215 dollars Brooklyn, Fort Greene Jane June 28 2019 Perfect for Your Parents + Garden Entire home/apt 7322 140 dollars Manhattan, Chelsea Doti July 01 2019 Chelsea Perfect Private room 7726 99 dollars Brooklyn, Crown Heights Adam And Charity June 22 2019 Hip Historic Brownstone Apartment with Backyard Entire home/apt 8024 130 dollars Brooklyn, Park Slope Lisel July 01 2019 CBG CtyBGd HelpsHaiti rm#1:1-4 PRIVATE ROOM 8025 80 dollars Brooklyn, Park Slope Lisel January 01 2019 CBG Helps Haiti Room#2.5 PRIVATE ROOM 8110 110 dollars Brooklyn, Park Slope Lisel July 02 2019 CBG Helps Haiti Rm #2 Private room 8490 120 dollars Brooklyn, Bedford-Stuyvesant Nathalie June 19 2019 MAISON DES SIRENES1,bohemian apartment Entire home/apt 8505 60 dollars Brooklyn, Windsor Terrace Gregory June 23 2019 Sunny Bedroom Across Prospect Park Private room 9518 44 dollars Manhattan, Inwood Shon June 15 2019 SPACIOUS, LOVELY FURNISHED MANHATTAN BEDROOM PRIVATE ROOM 9657 180 dollars Manhattan, East Village Dana April 19 2019 Modern 1 BR / NYC / EAST VILLAGE entire home/apt 9668 50 dollars Manhattan, Harlem Ssameer Or Trip June 01 2019 front room/double bed PRIVATE ROOM 9704 52 dollars Manhattan, Harlem Teri June 14 2019 Spacious 1 bedroom in luxe building Private room 9782 55 dollars Brooklyn, Greenpoint Andrea June 15 2019 Loft in Williamsburg Area w/ Roof Private room 9783 50 dollars Manhattan, Harlem Ssameer Or Trip July 01 2019 back room/bunk beds Private room 10452 70 dollars Brooklyn, Bedford-Stuyvesant Angela May 12 2019 Large B&B Style rooms Private room 10962 89 dollars Brooklyn, South Slope Laurie June 21 2019 Lovely room 2 & garden; Best area, Legal rental Private room 11708 85 dollars Brooklyn, Bushwick Tyrome June 22 2019 Cute apt in artist's home Entire home/apt 12048 40 dollars Manhattan, Lower East Side Ben July 05 2019 LowerEastSide apt share shortterm 1 shared room 12192 68 dollars Manhattan, East Village Edward June 21 2019 ENJOY Downtown NYC! PRIVATE ROOM 12299 120 dollars Brooklyn, South Slope Abdul May 27 2019 Beautiful Sunny Park Slope Brooklyn Entire home/apt 12318 135 dollars Manhattan, Upper West Side Cyn June 16 2019 West Side Retreat Private room 12343 150 dollars Manhattan, Harlem Earl June 13 2019 BEST BET IN HARLEM Entire home/apt 12627 150 dollars Brooklyn, Prospect-Lefferts Gardens Rana June 05 2019 Entire apartment in central Brooklyn neighborhood. Entire home/apt 12937 130 dollars Queens, Long Island City Orestes July 01 2019 1 Stop fr. Manhattan! Private Suite,Landmark Block private room 12940 110 dollars Brooklyn, Bedford-Stuyvesant Adreinne May 25 2019 Charming Brownstone 3 - Near PRATT Entire home/apt 13394 80 dollars Brooklyn, Fort Greene Alexander June 17 2019 Fort Greene brownstone Private room 13808 80 dollars Brooklyn, Bedford-Stuyvesant JT 

In [0]:
from pyspark.sql.functions import min, max, col

# Establecemos la columna last review
df2 = combined_df.withColumn("last_review", col("last_review").cast("date"))
df2.printSchema()

# Obtener la fecha de la primera y la última reseña
primera_reseña = combined_df.agg(min("last_review")).collect()[0][0]
última_reseña = combined_df.agg(max("last_review")).collect()[0][0]

# Guardamos los datos en las variables
fecha_primera_reseña = primera_reseña
fecha_última_reseña = última_reseña

# Mostramos las fechas
print("Fecha de la primera reseña:", fecha_primera_reseña)
print("Fecha de la última reseña:", fecha_última_reseña)


root
 |-- listing_id: integer (nullable = true)
 |-- price: string (nullable = true)
 |-- nbhood_full: string (nullable = true)
 |-- host_name: string (nullable = true)
 |-- last_review: date (nullable = true)
 |-- description: string (nullable = true)
 |-- room_type: string (nullable = true)

Fecha de la primera reseña: April 01 2019
Fecha de la última reseña: May 31 2019


In [0]:
# Hacemos un filtro para contar las habitqaciones privadas
num_habitaciones_privadas = combined_df.filter(col("room_type") == "Private room").count()

#Lo guardamos en una variable 
habitaciones_privadas= num_habitaciones_privadas

# Mostramos el resultado
print("Número de anuncios que son habitaciones privadas:",habitaciones_privadas)


Número de anuncios que son habitaciones privadas: 7241


In [0]:
from pyspark.sql.functions import avg, round, col, regexp_replace

#  Creamos una nueva columna donde eliminamos la palabra "dollars" y convertipos el precio a double
combined_df = combined_df.withColumn("price_numeric", regexp_replace(col("price"), " dollars", "").cast("double"))

# Mostrar el esquema después de la transformación para comprobar que se a cambiado a double
combined_df.printSchema()
combined_df.display()

# Calculamos el precio promedio y redondeamos a dos decimales
precio_promedio = combined_df.agg(round(avg("price_numeric"), 2)).collect()[0][0]

#Lo guardamos en una variable
media_precios = precio_promedio

# Mostramos el precio promedio
print("Precio promedio de los anuncios:", media_precios)


root
 |-- listing_id: integer (nullable = true)
 |-- price: string (nullable = true)
 |-- nbhood_full: string (nullable = true)
 |-- host_name: string (nullable = true)
 |-- last_review: string (nullable = true)
 |-- description: string (nullable = true)
 |-- room_type: string (nullable = true)
 |-- price_numeric: double (nullable = true)



listing_id price nbhood_full host_name last_review description room_type price_numeric 2595 225 dollars Manhattan, Midtown Jennifer May 21 2019 Skylit Midtown Castle Entire home/apt 225.0 3831 89 dollars Brooklyn, Clinton Hill LisaRoxanne July 05 2019 Cozy Entire Floor of Brownstone Entire home/apt 89.0 5099 200 dollars Manhattan, Murray Hill Chris June 22 2019 Large Cozy 1 BR Apartment In Midtown East Entire home/apt 200.0 5178 79 dollars Manhattan, Hell's Kitchen Shunichi June 24 2019 Large Furnished Room Near B'way private room 79.0 5238 150 dollars Manhattan, Chinatown Ben June 09 2019 Cute & Cozy Lower East Side 1 bdrm Entire home/apt 150.0 5295 135 dollars Manhattan, Upper West Side Lena June 22 2019 Beautiful 1br on Upper West Side Entire home/apt 135.0 5441 85 dollars Manhattan, Hell's Kitchen Kate June 23 2019 Central Manhattan/near Broadway Private room 85.0 5803 89 dollars Brooklyn, South Slope Laurie June 24 2019 Lovely Room 1, Garden, Best Area, Legal rental Private room 89.0 6021 85 dollars Manhattan, Upper West Side Claudio July 05 2019 Wonderful Guest Bedroom in Manhattan for SINGLES Private room 85.0 6848 140 dollars Brooklyn, Williamsburg Allen & Irina June 29 2019 Only 2 stops to Manhattan studio entire home/apt 140.0 7097 215 dollars Brooklyn, Fort Greene Jane June 28 2019 Perfect for Your Parents + Garden Entire home/apt 215.0 7322 140 dollars Manhattan, Chelsea Doti July 01 2019 Chelsea Perfect Private room 140.0 7726 99 dollars Brooklyn, Crown Heights Adam And Charity June 22 2019 Hip Historic Brownstone Apartment with Backyard Entire home/apt 99.0 8024 130 dollars Brooklyn, Park Slope Lisel July 01 2019 CBG CtyBGd HelpsHaiti rm#1:1-4 PRIVATE ROOM 130.0 8025 80 dollars Brooklyn, Park Slope Lisel January 01 2019 CBG Helps Haiti Room#2.5 PRIVATE ROOM 80.0 8110 110 dollars Brooklyn, Park Slope Lisel July 02 2019 CBG Helps Haiti Rm #2 Private room 110.0 8490 120 dollars Brooklyn, Bedford-Stuyvesant Nathalie June 19 2019 MAISON DES SIRENES1,bohemian apartment Entire home/apt 120.0 8505 60 dollars Brooklyn, Windsor Terrace Gregory June 23 2019 Sunny Bedroom Across Prospect Park Private room 60.0 9518 44 dollars Manhattan, Inwood Shon June 15 2019 SPACIOUS, LOVELY FURNISHED MANHATTAN BEDROOM PRIVATE ROOM 44.0 9657 180 dollars Manhattan, East Village Dana April 19 2019 Modern 1 BR / NYC / EAST VILLAGE entire home/apt 180.0 9668 50 dollars Manhattan, Harlem Ssameer Or Trip June 01 2019 front room/double bed PRIVATE ROOM 50.0 9704 52 dollars Manhattan, Harlem Teri June 14 2019 Spacious 1 bedroom in luxe building Private room 52.0 9782 55 dollars Brooklyn, Greenpoint Andrea June 15 2019 Loft in Williamsburg Area w/ Roof Private room 55.0 9783 50 dollars Manhattan, Harlem Ssameer Or Trip July 01 2019 back room/bunk beds Private room 50.0 10452 70 dollars Brooklyn, Bedford-Stuyvesant Angela May 12 2019 Large B&B Style rooms Private room 70.0 10962 89 dollars Brooklyn, South Slope Laurie June 21 2019 Lovely room 2 & garden; Best area, Legal rental Private room 89.0 11708 85 dollars Brooklyn, Bushwick Tyrome June 22 2019 Cute apt in artist's home Entire home/apt 85.0 12048 40 dollars Manhattan, Lower East Side Ben July 05 2019 LowerEastSide apt share shortterm 1 shared room 40.0 12192 68 dollars Manhattan, East Village Edward June 21 2019 ENJOY Downtown NYC! PRIVATE ROOM 68.0 12299 120 dollars Brooklyn, South Slope Abdul May 27 2019 Beautiful Sunny Park Slope Brooklyn Entire home/apt 120.0 12318 135 dollars Manhattan, Upper West Side Cyn June 16 2019 West Side Retreat Private room 135.0 12343 150 dollars Manhattan, Harlem Earl June 13 2019 BEST BET IN HARLEM Entire home/apt 150.0 12627 150 dollars Brooklyn, Prospect-Lefferts Gardens Rana June 05 2019 Entire apartment in central Brooklyn neighborhood. Entire home/apt 150.0 12937 130 dollars Queens, Long Island City Orestes July 01 2019 1 Stop fr. Manhattan! Private Suite,Landmark Block private room 130.0 12940 110 dollars Brooklyn, Bedford-Stuyvesant Adreinne May 25 201

Precio promedio de los anuncios: 141.78


In [0]:
from pyspark.sql import Row
from pyspark.sql.functions import count

# Creamos una fila con las variables de los ej anteriores
data = Row(first_reviewed=fecha_primera_reseña, 
            last_reviewed=fecha_última_reseña, 
            nb_private_rooms=habitaciones_privadas, 
            avg_price=media_precios)

# Crear el DataFrame review_dates con una unica fila
df_final = spark.createDataFrame([data])

# Mostrar el DataFrame
df_final.show()

+--------------+-------------+----------------+---------+
|first_reviewed|last_reviewed|nb_private_rooms|avg_price|
+--------------+-------------+----------------+---------+
| April 01 2019|  May 31 2019|            7241|   141.78|
+--------------+-------------+----------------+---------+

